# __Using a Speech Recognition Model__

- Tutorial Difficulty: ★☆☆☆☆
- 5 min read
- Languages: [SQL](https://en.wikipedia.org/wiki/SQL) (100%)
- File Location: tutorial_en/thanosql_ml/audio_recognition/speech_recognition2.ipynb
- References: [(AI-Hub) Korean voice data](https://aihub.or.kr/aihubdata/data/view.do?currMenu=115&topMenu=100&aihubDataSe=realm&dataSetSn=123), [whisper](https://github.com/openai/whisper)

## Tutorial Introduction

<div class="admonition note">
    <h4 class="admonition-title">Understanding Speech Recognition</h4>
    <p>Speech recognition technology, also called computer speech recognition or speech-to-text, allows programs to process human speech into text format. Recently, it has been used in a wide range of fields such as automobiles, medical fields, and everyday life involving artificial intelligence speakers and smartphones. Recent <a href="https://en.wikipedia.org/wiki/Machine_learning">Machine Learning</a> Speech recognition technology utilizes algorithms that understand and process speech by integrating grammar, syntax, structure, and composition of audio and speech signals.</p>
</div>

<div class="admonition warning">
    <p>Speech Recognition should not be confused with Voice Recognition, which focuses only on identifying the individual users' voices.</p>
</div>

Today, speech recognition technology is being applied in various industries. Advances in speech recognition technology have been expanding into automatic interpretation for simple travel to high-level business meetings. In addition, it has delved into fields such as speech synthesis technology, which acts as a virtual guide, mimicking the voice of a specific celebrity, and converting a predetermined fingerprint into a voice.

__The following are examples and applications of the ThanoSQL speech recognition model.__

- Speech recognition technology converts phone consultation data into text to enable customer sentiment analysis and consultation trend analysis. Using speech recognition technology, customer service representatives can improve their service by quickly receiving relevant information that answers customer inquiries.
In addition, after consultation, the customer satisfaction trend can be analyzed even with the indirect measurement of customer satisfaction through sentiment analysis.

- Using speech recognition technology, you can write notes faster than writing with a keyboard and instantly search for specific keywords even in long audio files.

<div class="admonition note">
    <h4 class="admonition-title">In This Tutorial</h4>
    <p>👉 <strong>Whisper</strong> [Alec Radford et al. 2022] is a general-purpose speech recognition deep learning model released by OpenAI that supports learning on large datasets of various audio and is a multi-task model that enables both translation and transcription as well as multilingual speech recognition. It also performs well and is widely used for common speech recognition problems. In this tutorial, <strong>Whisper</strong>'s speech recognition and translation into English will be performed.
    </p>
</div>

## __0. Prepare Dataset and Model__

As mentioned in the [ThanoSQL Workspace](https://docs.thanosql.ai/1.5/en/getting_started/paas/workspace/lab/), you must create an API token and run the query below to execute the query of ThanoSQL. 

In [ ]:
%load_ext thanosql
%thanosql API_TOKEN=<Issued_API_TOKEN>

### __Prepare Dataset__

In [2]:
%%thanosql
GET THANOSQL DATASET korean_voice_data
OPTIONS (overwrite=True)

Success


<div class="admonition note">
    <h4 class="admonition-title">Query Details</h4>
    <ul>
        <li>"<strong>GET THANOSQL DATASET</strong>" downloads the specified dataset to the workspace.</li>
        <li>"<strong>OPTIONS</strong>" specifies the option values to be used for the <strong>GET THANOSQL DATASET</strong> clause.
        <ul>
            <li>"overwrite": determines whether to overwrite a dataset if it already exists. If set as True, the old dataset is replaced with the new dataset (bool, optional, True|False, default: False)</li>
        </ul>
        </li>
    </ul>
</div>

In [3]:
%%thanosql
COPY korean_voice
OPTIONS (if_exists='replace')
FROM 'thanosql-dataset/korean_voice_data/korean_voice.csv'

Success


<div class="admonition note">
    <h4 class="admonition-title">Query Details</h4>
    <ul>
        <li>"<strong>COPY</strong>" specifies the name of the dataset to be saved as a database table.</li>
        <li>"<strong>OPTIONS</strong>" specifies the option values to be used for the <strong>COPY</strong> clause.
        <ul>
           <li>"if_exists": determines how the function should handle the case where the table already exists, it can either raise an error, append to the existing table, or replace the existing table (str, optional, 'fail'|'replace'|'append', default: 'fail')</li>
        </ul>
        </li>
    </ul>
</div>

### __Prepare the Model__

In [4]:
%%thanosql
GET THANOSQL MODEL whisper_s
OPTIONS (
    model_name='tutorial_whisper_small',
    overwrite=True
    )

Success


<div class="admonition note">
    <h4 class="admonition-title">Query Details</h4>
    <ul>
        <li>"<strong>GET THANOSQL MODEL</strong>" downloads the specified model to the workspace.</li>
        <li>"<strong>OPTIONS</strong>" specifies the option values to be used for the <strong>GET THANOSQL MODEL</strong> clause.
        <ul>
            <li>"model_name": the model name to store a given model in the ThanoSQL workspace (str, optional)</li>
            <li>"overwrite": determines whether to overwrite a model if it already exists. If set as True, the old model is replaced with the new model (bool, optional, True|False, default: False)</li>
        </ul>
        </li>
    </ul>
</div>

## __1. Check Dataset__

For this tutorial, we use the __korean_voice__ table stored in the ThanoSQL workspace database. Execute the query below to check the contents of the table.

In [5]:
%%thanosql
SELECT *
FROM korean_voice
LIMIT 5

audio_path  sampling_rate  \
0  thanosql-dataset/korean_voice_data/audio/broad...          16000   
1  thanosql-dataset/korean_voice_data/audio/broad...          16000   
2  thanosql-dataset/korean_voice_data/audio/broad...          16000   
3  thanosql-dataset/korean_voice_data/audio/broad...          16000   
4  thanosql-dataset/korean_voice_data/audio/broad...          16000   

                                 transcript_phonetic  \
0  가를 보면 한국어 사용하는 인구 수가 십이 위입니다. 일위가 중국어고 이위가 스페인...   
1                    말을 사랑하고 아껴서 규정에 맞게 파괴하지 않고 네 잘.   
2       진행하고 있습니다. 자 오늘의 목표 확인해 보도록 하겠습니다. 오늘의 목표 네.   
3                그리고 이번에는 다른 친구의 글을 평가해보는 것을 하는 겁니다.   
4  쓰기가 된 글 완성된 글 또는 쓰기 전의 개요 뭐 자료 이런 것들을 보여주면서 그것...   

                                 transcript_spelling  duration  
0  가를 보면 한국어 사용하는 인구 수가 십이 위입니다. 일위가 중국어고 이위가 스페인...      8.70  
1                    말을 사랑하고 아껴서 규정에 맞게 파괴하지 않고 네 잘.      5.89  
2       진행하고 있습니다. 자 오늘의 목표 확인해 보도록 하겠습니다. 오늘의 목표 네.      4.86  
3                그리고 이번에는 다른 친구의 글을 평가해보는 것을 하는 겁니다.      4.61  
4  쓰기가 된 글 완성된 글 또는 쓰기 전의 개요 뭐 자료 이런 것들을 보여주면서 그것...     11.52

<div class="admonition note">
    <h4 class="admonition-title">Understanding the Data Table</h4>
    <p><strong>korean_voice</strong> table contains the following information.</p>
    <ul>
        <li>audio_path: the audio file's path</li>
        <li>transcript_spelling: target value of the corresponding audio(target, script)</li>
        <li>transcript_phonetic: the visual representation of speech sounds(or phones) by means of symbols</li>
    </ul>
</div>

In [6]:
%%thanosql
PRINT AUDIO
AS
SELECT audio_path
FROM korean_voice
LIMIT 3

/home/jovyan/thanosql-dataset/korean_voice_data/audio/broadcast_00033030.flac


/home/jovyan/thanosql-dataset/korean_voice_data/audio/broadcast_00033057.flac


/home/jovyan/thanosql-dataset/korean_voice_data/audio/broadcast_00033066.flac


## __2. Predict Using Pre-built Model__

To transcribe the audio results using the __tutorial_whisper_small__ model, run the following query.

- `task='transcribe'` When this option is specified, speech recognition is performed. 

In [7]:
%%thanosql
PREDICT USING tutorial_whisper_small
OPTIONS (
    audio_col='audio_path',
    language='auto',
    task='transcribe',
    result_col='predict_result'
    )
AS
SELECT *
FROM korean_voice

audio_path  sampling_rate  \
0   thanosql-dataset/korean_voice_data/audio/broad...          16000   
1   thanosql-dataset/korean_voice_data/audio/broad...          16000   
2   thanosql-dataset/korean_voice_data/audio/broad...          16000   
3   thanosql-dataset/korean_voice_data/audio/broad...          16000   
4   thanosql-dataset/korean_voice_data/audio/broad...          16000   
..                                                ...            ...   
95  thanosql-dataset/korean_voice_data/audio/broad...          16000   
96  thanosql-dataset/korean_voice_data/audio/broad...          16000   
97  thanosql-dataset/korean_voice_data/audio/broad...          16000   
98  thanosql-dataset/korean_voice_data/audio/broad...          16000   
99  thanosql-dataset/korean_voice_data/audio/broad...          16000   

                                  transcript_phonetic  \
0   가를 보면 한국어 사용하는 인구 수가 십이 위입니다. 일위가 중국어고 이위가 스페인...   
1                     말을 사랑하고 아껴서 규정에 맞게 파괴하지 않고 네 잘.   
2        진행하고 있습니다. 자 오늘의 목표 확인해 보도록 하겠습니다. 오늘의 목표 네.   
3                 그리고 이번에는 다른 친구의 글을 평가해보는 것을 하는 겁니다.   
4   쓰기가 된 글 완성된 글 또는 쓰기 전의 개요 뭐 자료 이런 것들을 보여주면서 그것...   
..                                                ...   
95                        희곡 같은 데서 제일 중요한 한 단어는 뭐라고요.   
96                           수필이라는 이름 자체가 무슨 뜻인지 아나요.   
97              당근 씨를 막 뿌리려는 남편에게 나는 몇 번이나 말했다 그랬습니다.   
98                 작년에도 너무 얕게 씨를 뿌려 낭패를 본 적이 있기 때문이다.   
99                                  하나는 새를 위해서 하나는 또.   

                                  transcript_spelling  duration  \
0   가를 보면 한국어 사용하는 인구 수가 십이 위입니다. 일위가 중국어고 이위가 스페인...      8.70   
1                     말을 사랑하고 아껴서 규정에 맞게 파괴하지 않고 네 잘.      5.89   
2        진행하고 있습니다. 자 오늘의 목표 확인해 보도록 하겠습니다. 오늘의 목표 네.      4.86   
3                 그리고 이번에는 다른 친구의 글을 평가해보는 것을 하는 겁니다.      4.61   
4   쓰기가 된 글 완성된 글 또는 쓰기 전의 개요 뭐 자료 이런 것들을 보여주면서 그것...     11.52   
..                                                ...       ...   
95                        희곡 같은 데서 제일 중요한 한 단어는 뭐라고요.      3.20   
96                           수필이라는 이름 자체가 무슨 뜻인지 아나요.      2.94   
97              당근 씨를 막 뿌리려는 남편에게 나는 몇 번이나 말했다 그랬습니다.      3.58   
98                 작년에도 너무 얕게 씨를 뿌려 낭패를 본 적이 있기 때문이다.      4.22   
99                                  하나는 새를 위해서 하나는 또.      2.69   

                                       predict_result  
0   가를 보면 한국어 사용하는 인구수가 12위입니다 1위가 중국어고 2위가 스페인어고 ...  
1                         를 사랑하고 아껴서 규정에 맞게 파괴하지 않고 잘  
2                                오늘의 목표 확인해보도록 하겠습니다.  
3                  그리고 이번에는 다른 친구에게를 평가해 보는 것을 하는 겁니다  
4   쓰기가 될 글 완성된 글 또는 쓰기 전에 개요, 자료 이런 것들을 보여주면서 그것을...  
..                                                ...  
95                       키곡 같은 데에서 제일 중요한 한 단어는 뭐라고요?  
96                           수필이라는 이름 자체가 무슨 뜻인지 알아요?  
97                     당근실을 막 뿌리려는 남편에게 나는 몇 번이나 말했다.  
98                 작년에도 너무 얕게 씨를 뿌려 낭패를 본 적이 있기 때문이다.  
99                                       하나는 새, 하나는 또  

[100 rows x 6 columns]

<div class="admonition note">
    <h4 class="admonition-title">Query Details</h4>
    <ul>
        <li>"<strong>PREDICT USING</strong>" predicts the outcome using the <strong>tutorial_whisper_small</strong>.
        <li>"<strong>OPTIONS</strong>" specifies the option values to be used for prediction.
        <ul>
            <li>"audio_col": the name of the column containing the audio path to be used for prediction (str, default: 'audio_path')</li>
            <li>"batch_size": the size of the dataset bundle read during a single train (int, optional, default: 16)</li>
            <li>"language": specifies the language of the audio file. If selected as ‘auto’, the model will recognize the language from the available pool of 99 languages (str, default: 'auto')</li>
            <li>"task": type of work to do (str, 'transcribe'|'translate', default: 'transcribe')</li>
            <li>"result_col": the column that contains the predicted results (str, optional, default: 'predict_result')</li>
        </ul>
        </li>
    </ul>
</div>

## __3. Translate to English Using Pre-built Model__

To auto-translate the audio results using the __tutorial_whisper_small__ model, run the following query.

- `task='translate'` When this option is specified, speech recognition is performed. This process translates "Korean speech" directly into "English text," which is different from general translations in that it does not require the extra step of using "Korean text" during the process.

In [8]:
%%thanosql
PREDICT USING tutorial_whisper_small
OPTIONS (
    audio_col='audio_path',
    language='auto',
    task='translate',
    result_col='predict_result'
    )
AS
SELECT *
FROM korean_voice

audio_path  sampling_rate  \
0   thanosql-dataset/korean_voice_data/audio/broad...          16000   
1   thanosql-dataset/korean_voice_data/audio/broad...          16000   
2   thanosql-dataset/korean_voice_data/audio/broad...          16000   
3   thanosql-dataset/korean_voice_data/audio/broad...          16000   
4   thanosql-dataset/korean_voice_data/audio/broad...          16000   
..                                                ...            ...   
95  thanosql-dataset/korean_voice_data/audio/broad...          16000   
96  thanosql-dataset/korean_voice_data/audio/broad...          16000   
97  thanosql-dataset/korean_voice_data/audio/broad...          16000   
98  thanosql-dataset/korean_voice_data/audio/broad...          16000   
99  thanosql-dataset/korean_voice_data/audio/broad...          16000   

                                  transcript_phonetic  \
0   가를 보면 한국어 사용하는 인구 수가 십이 위입니다. 일위가 중국어고 이위가 스페인...   
1                     말을 사랑하고 아껴서 규정에 맞게 파괴하지 않고 네 잘.   
2        진행하고 있습니다. 자 오늘의 목표 확인해 보도록 하겠습니다. 오늘의 목표 네.   
3                 그리고 이번에는 다른 친구의 글을 평가해보는 것을 하는 겁니다.   
4   쓰기가 된 글 완성된 글 또는 쓰기 전의 개요 뭐 자료 이런 것들을 보여주면서 그것...   
..                                                ...   
95              당근 씨를 막 뿌리려는 남편에게 나는 몇 번이나 말했다 그랬습니다.   
96                 작년에도 너무 얕게 씨를 뿌려 낭패를 본 적이 있기 때문이다.   
97                                  하나는 새를 위해서 하나는 또.   
98    많이 씨앗들을 넣어가지고 너무 촘촘하게 여러 개가 한꺼번에 자라는 거야 여러 줄기가.   
99                                   텃밭 농사짓는 정도일 겁니다.   

                                  transcript_spelling  duration  \
0   가를 보면 한국어 사용하는 인구 수가 십이 위입니다. 일위가 중국어고 이위가 스페인...      8.70   
1                     말을 사랑하고 아껴서 규정에 맞게 파괴하지 않고 네 잘.      5.89   
2        진행하고 있습니다. 자 오늘의 목표 확인해 보도록 하겠습니다. 오늘의 목표 네.      4.86   
3                 그리고 이번에는 다른 친구의 글을 평가해보는 것을 하는 겁니다.      4.61   
4   쓰기가 된 글 완성된 글 또는 쓰기 전의 개요 뭐 자료 이런 것들을 보여주면서 그것...     11.52   
..                                                ...       ...   
95              당근 씨를 막 뿌리려는 남편에게 나는 몇 번이나 말했다 그랬습니다.      3.58   
96                 작년에도 너무 얕게 씨를 뿌려 낭패를 본 적이 있기 때문이다.      4.22   
97                                  하나는 새를 위해서 하나는 또.      2.69   
98    많이 씨앗들을 넣어가지고 너무 촘촘하게 여러 개가 한꺼번에 자라는 거야 여러 줄기가.      6.14   
99                                   텃밭 농사짓는 정도일 겁니다.      2.30   

                                       predict_result  
0            The number of people using Korean is 12.  
1   Love and cherish the words and don't destroy t...  
2                           Let's check today's goal.  
3   And this time, I'm going to evaluate other fri...  
4      It is a problem of the order and writing area.  
..                                                ...  
95  I told my husband that I would pour carrots a ...  
96  I've seen a lot of people who put too little s...  
97  One is for the new year. Another is for the ne...  
98  I put a lot of seeds in it and it grew into a ...  
99  It's about the same as the picture in the Tupp...  

[100 rows x 6 columns]

<div class="admonition note">
    <h4 class="admonition-title">Query Details</h4>
    <ul>
        <li>"<strong>PREDICT USING</strong>" predicts the outcome using the <strong>tutorial_whisper_small</strong>.
        <li>"<strong>OPTIONS</strong>" specifies the option values to be used for prediction.
        <ul>
            <li>"audio_col": the name of the column containing the audio path to be used for prediction (str, default: 'audio_path')</li>
            <li>"batch_size": the size of the dataset bundle read during a single train (int, optional, default: 16)</li>
            <li>"language": specifies the language of the audio file. If selected as ‘auto’, the model will recognize the language from the available pool of 99 languages (str, default: 'auto')</li>
            <li>"task": type of work to do (str, 'transcribe'|'translate', default: 'transcribe')</li>
            <li>"result_col": the column that contains the predicted results (str, optional, default: 'predict_result')</li>
        </ul>
        </li>
    </ul>
</div>

## __4. In Conclusion__
 
In this tutorial, we used the __Whisper__ model for speech recognition and translation using the korean_voice dataset. As this is a beginner-level tutorial, we focused on the process rather than accuracy.

* [How to Upload My Data to the ThanoSQL Workspace](https://docs.thanosql.ai/1.5/en/getting_started/data_upload/)
* [How to Create a Table Using My Data](https://docs.thanosql.ai/1.5/en/how-to_guides/ThanoSQL_query/COPY_SYNTAX/)
* [How to Upload My Model to the ThanoSQL Workspace](https://docs.thanosql.ai/1.5/en/how-to_guides/ThanoSQL_query/UPLOAD_MODEL_SYNTAX/)

<div class="admonition tip">
    <h4 class="admonition-title">Inquiries About Deploying a Model for Your Own Service</h4>
    <p>If you have any difficulties creating your own model using ThanoSQL or applying it to your service, please feel free to contact us below😊</p>
    <p>For inquiries regarding building a speech recognition model: <a href="mailto:contact@smartmind.team">contact@smartmind.team</a></p>
</div>